In [86]:
from sklearn.preprocessing import LabelEncoder
from sklearn.ensemble import RandomForestClassifier
import pandas as pd
import random
import os
import numpy as np
import matplotlib.pyplot as plt
import warnings; warnings.filterwarnings(action='ignore')
import pickle
import time

from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import VotingClassifier
#from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
import sklearn.svm as svm
import xgboost as xgb

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from bayes_opt import BayesianOptimization
from matplotlib_venn import venn2, venn2_circles

from xgboost import plot_importance
from scipy.stats import randint
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score
from sklearn.metrics import accuracy_score

In [87]:
def seed_everything(seed):
    random.seed(seed) #파이썬 자체 모듈 random 모듈의 시드 고정
    os.environ['PYTHONHASHSEED'] = str(seed) 
    np.random.seed(seed) #넘파이를 사용할 경우
#     torch.manual_seed(seed)
#     torch.cuda.manual_seed(seed)
#     torch.backends.cudnn.deterministic = True
    
seed_everything(37) # Seed 고정

In [88]:
# Preprocessing 전처리한 데이터 train_pp, test_pp
train_a = pd.read_csv('./data/train_a.csv')
train_to = pd.read_csv('./data/train_to.csv')
traina_pp = pd.read_csv('./data/imputed_a_1val_highcorr.csv')
trainto_pp = pd.read_csv('./data/imputed_to_1val_highcorr.csv')

test = pd.read_csv('./data/test.csv')
test_a = test[test['PRODUCT_CODE']=='A_31']
test_to = test[(test['PRODUCT_CODE']=='T_31')|(test['PRODUCT_CODE']=='O_31')]

In [ ]:
train_a.head()

# 데이터 준비

train데이터로 학습한 모델로 test데이터의 예측을 진행하므로 train의 컬럼만 test데이터에 넣는다.

In [113]:
testa_df = test_a[traina_pp.columns]
testto_df = test_to[trainto_pp.columns]

In [114]:
train_y = train_a['Y_Class']

In [115]:
train_x = pd.concat([train_a[['LINE', 'PRODUCT_CODE']],traina_pp], axis = 1)
train_x.head()

LINE PRODUCT_CODE   X_128    X_130  X_132  X_133  X_136  X_143   X_144  \
0  T050304         A_31  7813.0  13151.4   0.19   0.20  228.0    0.0  249.96   
1  T050307         A_31  8541.0  19854.0   0.20   0.21  413.0    0.0  249.97   
2  T050304         A_31  7815.0  11472.0   0.19   0.20  228.0    0.0  249.97   
3  T050307         A_31  8541.0  19856.0   0.20   0.21  414.0    0.0  249.97   
4  T050304         A_31  7817.0  11569.0   0.19   0.20  228.0    0.0  249.96   

    X_146  ...  X_2792  X_2793  X_2796     X_2797  X_2798     X_2800  X_2801  \
0  247.46  ...    21.0    24.0    24.0  22.592593    21.0  22.925926    20.0   
1  249.43  ...    22.0    25.0    25.0  23.600000    22.0  25.050000    24.0   
2  249.10  ...    22.0    24.0    25.0  23.370370    22.0  23.962963    22.0   
3  243.26  ...    22.0    25.0    25.0  23.592593    22.0  25.037037    23.0   
4  246.46  ...    22.0    24.0    25.0  23.296296    22.0  24.000000    22.0   

   X_2839  X_2840    X_2842  
0    5.02    7.00  0.000331  
1    5.00    7.05  0.001150  
2    5.02    6.52  0.000332  
3    5.01    7.03  0.001210  
4    5.03    6.52  0.000334  

[5 rows x 479 columns]

In [116]:
test_x = pd.concat([test_a[['LINE', 'PRODUCT_CODE']],testa_df], axis = 1)
test_x.head()

LINE PRODUCT_CODE    X_128  X_130  X_132  X_133  X_136  X_143   X_144  \
3  T010305         A_31      NaN    NaN    NaN    NaN    NaN    NaN     NaN   
4  T010306         A_31      NaN    NaN    NaN    NaN    NaN    NaN     NaN   
5  T010306         A_31      NaN    NaN    NaN    NaN    NaN    NaN     NaN   
6  T010305         A_31      NaN    NaN    NaN    NaN    NaN    NaN     NaN   
7  T050304         A_31  18031.0    NaN   0.19    0.2  354.0    0.0  249.96   

    X_146  ...  X_2792  X_2793  X_2796     X_2797  X_2798     X_2800  X_2801  \
3     NaN  ...     NaN     NaN     NaN        NaN     NaN        NaN     NaN   
4     NaN  ...     NaN     NaN     NaN        NaN     NaN        NaN     NaN   
5     NaN  ...     NaN     NaN     NaN        NaN     NaN        NaN     NaN   
6     NaN  ...     NaN     NaN     NaN        NaN     NaN        NaN     NaN   
7  246.56  ...    23.0    25.0    25.0  23.607143    22.0  24.785714    22.0   

   X_2839  X_2840    X_2842  
3     NaN     NaN       NaN  
4     NaN     NaN       NaN  
5     NaN     NaN       NaN  
6     NaN     NaN       NaN  
7    5.02    7.02  0.000156  

[5 rows x 479 columns]

In [117]:
a_index = test_x.index.tolist() 

In [118]:
len(a_index)

67

### A 데이터 범주형 변수 라벨 인코딩

In [119]:
qual_col = ['LINE', 'PRODUCT_CODE']

for i in qual_col:
    le = LabelEncoder()
    le = le.fit(train_x[i]) #원래 column 값을 기준으로 fit.
    train_x[i] = le.transform(train_x[i]) #수치화, 수치로 변형

    for label in np.unique(test_x[i]): 
        if label not in le.classes_: 
            le.classes_ = np.append(le.classes_, label)
    test_x[i] = le.transform(test_x[i]) 
print('Done.')

Done.


## train_a 학습 및 test_a 예측

In [120]:
from xgboost import XGBClassifier
from sklearn.model_selection import GridSearchCV

xgb_model = XGBClassifier(n_estimators=1500)

X_train, X_test, y_train, y_test = train_test_split(train_x, train_y, 
                                                    test_size=0.3, 
                                                    stratify=train_y, 
                                                    random_state=37)

# 후보 파라미터 선정
params = {'max_depth':[5, 6, 7], #일반적으로 3~10
          'subsample':[0.75, 0.8, 0.85], #일반적으로 0.5 ~ 1
          'learning_rate':[0.08, 0.1, 0.12], #일반적으로 0.01 ~ 0.2
          'min_child_weight':[3], # 1보다 샘플수작으면 leaf node. 너무 크게 설정하면 언더피팅
          'reg_lambda': [1], #default 1, L2 규제
          'reg_alpha' : [0.2], #default 0, L1 규제  
          'min_split_loss':[0.05, 0.1, 0.15], #범위 0~무한대
          'colsample_bytree':[0.8, 0.9]} #일반적으로 0~1

# gridsearchcv 객체 정보 입력(어떤 모델, 파라미터 후보, 교차검증 몇 번)
gridcv = GridSearchCV(xgb_model, param_grid=params, cv=3)

# 파라미터 튜닝 시작 / eval_set: 학습은  (X_train, y_train), 검증은 (X_test, y_test)
gridcv.fit(X_train, y_train, early_stopping_rounds=50, eval_metric='mlogloss', eval_set=[(X_train, y_train), (X_test, y_test)])

#튜닝된 파라미터 출력
print(gridcv.best_params_)
print(gridcv.best_score_)

best_params = gridcv.best_params_
best_xgb_model = XGBClassifier(n_estimators=1500, **best_params)

# 훈련 데이터 전체에 대해 모델 학습
best_xgb_model.fit(X_train, y_train)

# 새로운 데이터에 대해 예측
preds = best_xgb_model.predict(test_x)

[0]	validation_0-mlogloss:1.05116	validation_1-mlogloss:1.08528
[1]	validation_0-mlogloss:1.00532	validation_1-mlogloss:1.06590
[2]	validation_0-mlogloss:0.96456	validation_1-mlogloss:1.04344
[3]	validation_0-mlogloss:0.93055	validation_1-mlogloss:1.03486
[4]	validation_0-mlogloss:0.89745	validation_1-mlogloss:1.03336
[5]	validation_0-mlogloss:0.86544	validation_1-mlogloss:1.01834
[6]	validation_0-mlogloss:0.83789	validation_1-mlogloss:1.00825
[7]	validation_0-mlogloss:0.81310	validation_1-mlogloss:1.00097
[8]	validation_0-mlogloss:0.79047	validation_1-mlogloss:0.99339
[9]	validation_0-mlogloss:0.77149	validation_1-mlogloss:0.99155
[10]	validation_0-mlogloss:0.75036	validation_1-mlogloss:0.99726
[11]	validation_0-mlogloss:0.72977	validation_1-mlogloss:0.98575
[12]	validation_0-mlogloss:0.71015	validation_1-mlogloss:0.97862
[13]	validation_0-mlogloss:0.69026	validation_1-mlogloss:0.97035
[14]	validation_0-mlogloss:0.67583	validation_1-mlogloss:0.96248
[15]	validation_0-mlogloss:0.66074	

[47]	validation_0-mlogloss:0.40876	validation_1-mlogloss:0.88516
[48]	validation_0-mlogloss:0.40511	validation_1-mlogloss:0.88763
[49]	validation_0-mlogloss:0.40225	validation_1-mlogloss:0.88763
[50]	validation_0-mlogloss:0.39924	validation_1-mlogloss:0.89089
[51]	validation_0-mlogloss:0.39523	validation_1-mlogloss:0.89070
[52]	validation_0-mlogloss:0.39298	validation_1-mlogloss:0.89302
[53]	validation_0-mlogloss:0.39091	validation_1-mlogloss:0.89245
[54]	validation_0-mlogloss:0.38732	validation_1-mlogloss:0.89322
[55]	validation_0-mlogloss:0.38494	validation_1-mlogloss:0.89292
[56]	validation_0-mlogloss:0.38209	validation_1-mlogloss:0.89247
[57]	validation_0-mlogloss:0.37973	validation_1-mlogloss:0.89094
[58]	validation_0-mlogloss:0.37753	validation_1-mlogloss:0.89213
[59]	validation_0-mlogloss:0.37575	validation_1-mlogloss:0.89128
[60]	validation_0-mlogloss:0.37390	validation_1-mlogloss:0.89234
[61]	validation_0-mlogloss:0.37192	validation_1-mlogloss:0.89449
[62]	validation_0-mloglos

[0]	validation_0-mlogloss:1.04865	validation_1-mlogloss:1.08871
[1]	validation_0-mlogloss:1.00538	validation_1-mlogloss:1.08260
[2]	validation_0-mlogloss:0.96324	validation_1-mlogloss:1.06056
[3]	validation_0-mlogloss:0.92700	validation_1-mlogloss:1.04786
[4]	validation_0-mlogloss:0.89321	validation_1-mlogloss:1.04591
[5]	validation_0-mlogloss:0.85909	validation_1-mlogloss:1.02881
[6]	validation_0-mlogloss:0.82932	validation_1-mlogloss:1.02071
[7]	validation_0-mlogloss:0.80318	validation_1-mlogloss:1.01256
[8]	validation_0-mlogloss:0.77557	validation_1-mlogloss:1.00081
[9]	validation_0-mlogloss:0.75547	validation_1-mlogloss:0.99466
[10]	validation_0-mlogloss:0.73321	validation_1-mlogloss:0.99217
[11]	validation_0-mlogloss:0.71342	validation_1-mlogloss:0.99094
[12]	validation_0-mlogloss:0.69503	validation_1-mlogloss:0.99241
[13]	validation_0-mlogloss:0.67684	validation_1-mlogloss:0.98646
[14]	validation_0-mlogloss:0.66013	validation_1-mlogloss:0.98134
[15]	validation_0-mlogloss:0.64517	

[47]	validation_0-mlogloss:0.40314	validation_1-mlogloss:0.91129
[48]	validation_0-mlogloss:0.40037	validation_1-mlogloss:0.91272
[49]	validation_0-mlogloss:0.39884	validation_1-mlogloss:0.91412
[50]	validation_0-mlogloss:0.39634	validation_1-mlogloss:0.90873
[51]	validation_0-mlogloss:0.39099	validation_1-mlogloss:0.90760
[52]	validation_0-mlogloss:0.38778	validation_1-mlogloss:0.91218
[53]	validation_0-mlogloss:0.38518	validation_1-mlogloss:0.91015
[54]	validation_0-mlogloss:0.38199	validation_1-mlogloss:0.91012
[55]	validation_0-mlogloss:0.37964	validation_1-mlogloss:0.90948
[56]	validation_0-mlogloss:0.37796	validation_1-mlogloss:0.90893
[57]	validation_0-mlogloss:0.37520	validation_1-mlogloss:0.90924
[58]	validation_0-mlogloss:0.37336	validation_1-mlogloss:0.91012
[59]	validation_0-mlogloss:0.37074	validation_1-mlogloss:0.91265
[60]	validation_0-mlogloss:0.36917	validation_1-mlogloss:0.91806
[61]	validation_0-mlogloss:0.36681	validation_1-mlogloss:0.92001
[62]	validation_0-mloglos

[12]	validation_0-mlogloss:0.68687	validation_1-mlogloss:0.99417
[13]	validation_0-mlogloss:0.66590	validation_1-mlogloss:0.99598
[14]	validation_0-mlogloss:0.64742	validation_1-mlogloss:0.99241
[15]	validation_0-mlogloss:0.63139	validation_1-mlogloss:0.99120
[16]	validation_0-mlogloss:0.61466	validation_1-mlogloss:0.98912
[17]	validation_0-mlogloss:0.60023	validation_1-mlogloss:0.98950
[18]	validation_0-mlogloss:0.58562	validation_1-mlogloss:0.98008
[19]	validation_0-mlogloss:0.57188	validation_1-mlogloss:0.98455
[20]	validation_0-mlogloss:0.56203	validation_1-mlogloss:0.98376
[21]	validation_0-mlogloss:0.55224	validation_1-mlogloss:0.98307
[22]	validation_0-mlogloss:0.54128	validation_1-mlogloss:0.98165
[23]	validation_0-mlogloss:0.52918	validation_1-mlogloss:0.97675
[24]	validation_0-mlogloss:0.51827	validation_1-mlogloss:0.97465
[25]	validation_0-mlogloss:0.50639	validation_1-mlogloss:0.97553
[26]	validation_0-mlogloss:0.49873	validation_1-mlogloss:0.97425
[27]	validation_0-mloglos

...

[18]	validation_0-mlogloss:0.50834	validation_1-mlogloss:0.90990
[19]	validation_0-mlogloss:0.49596	validation_1-mlogloss:0.90521
[20]	validation_0-mlogloss:0.48700	validation_1-mlogloss:0.90517
[21]	validation_0-mlogloss:0.47454	validation_1-mlogloss:0.90206
[22]	validation_0-mlogloss:0.46432	validation_1-mlogloss:0.89094
[23]	validation_0-mlogloss:0.45546	validation_1-mlogloss:0.89517
[24]	validation_0-mlogloss:0.44548	validation_1-mlogloss:0.88645
[25]	validation_0-mlogloss:0.43946	validation_1-mlogloss:0.88863
[26]	validation_0-mlogloss:0.43270	validation_1-mlogloss:0.88755
[27]	validation_0-mlogloss:0.42651	validation_1-mlogloss:0.88849
[28]	validation_0-mlogloss:0.42058	validation_1-mlogloss:0.88827
[29]	validation_0-mlogloss:0.41498	validation_1-mlogloss:0.88456
[30]	validation_0-mlogloss:0.40760	validation_1-mlogloss:0.88246
[31]	validation_0-mlogloss:0.40220	validation_1-mlogloss:0.88221
[32]	validation_0-mlogloss:0.39629	validation_1-mlogloss:0.89152
[33]	validation_0-mloglos

[63]	validation_0-mlogloss:0.35469	validation_1-mlogloss:1.08091
[0]	validation_0-mlogloss:1.02481	validation_1-mlogloss:1.08448
[1]	validation_0-mlogloss:0.95647	validation_1-mlogloss:1.06495
[2]	validation_0-mlogloss:0.90363	validation_1-mlogloss:1.03593
[3]	validation_0-mlogloss:0.85669	validation_1-mlogloss:1.02278
[4]	validation_0-mlogloss:0.81226	validation_1-mlogloss:1.01869
[5]	validation_0-mlogloss:0.77203	validation_1-mlogloss:0.99507
[6]	validation_0-mlogloss:0.73605	validation_1-mlogloss:0.98692
[7]	validation_0-mlogloss:0.70544	validation_1-mlogloss:0.97376
[8]	validation_0-mlogloss:0.67418	validation_1-mlogloss:0.96163
[9]	validation_0-mlogloss:0.65135	validation_1-mlogloss:0.95282
[10]	validation_0-mlogloss:0.62696	validation_1-mlogloss:0.94892
[11]	validation_0-mlogloss:0.60739	validation_1-mlogloss:0.95324
[12]	validation_0-mlogloss:0.58765	validation_1-mlogloss:0.96147
[13]	validation_0-mlogloss:0.56781	validation_1-mlogloss:0.95478
[14]	validation_0-mlogloss:0.55005	

[65]	validation_0-mlogloss:0.32439	validation_1-mlogloss:0.94650
[66]	validation_0-mlogloss:0.32501	validation_1-mlogloss:0.94602
[67]	validation_0-mlogloss:0.32460	validation_1-mlogloss:0.94376
[68]	validation_0-mlogloss:0.32429	validation_1-mlogloss:0.94422
[69]	validation_0-mlogloss:0.32375	validation_1-mlogloss:0.94631
[70]	validation_0-mlogloss:0.32311	validation_1-mlogloss:0.94726
[71]	validation_0-mlogloss:0.32258	validation_1-mlogloss:0.94672
[72]	validation_0-mlogloss:0.32292	validation_1-mlogloss:0.95044
[73]	validation_0-mlogloss:0.32228	validation_1-mlogloss:0.95092
[74]	validation_0-mlogloss:0.32102	validation_1-mlogloss:0.95221
[75]	validation_0-mlogloss:0.31978	validation_1-mlogloss:0.95342
[76]	validation_0-mlogloss:0.31941	validation_1-mlogloss:0.95643
[77]	validation_0-mlogloss:0.31838	validation_1-mlogloss:0.95600
[0]	validation_0-mlogloss:1.02413	validation_1-mlogloss:1.06831
[1]	validation_0-mlogloss:0.96439	validation_1-mlogloss:1.05627
[2]	validation_0-mlogloss:0

[44]	validation_0-mlogloss:0.36399	validation_1-mlogloss:0.99060
[45]	validation_0-mlogloss:0.36227	validation_1-mlogloss:0.99231
[46]	validation_0-mlogloss:0.36086	validation_1-mlogloss:0.99499
[47]	validation_0-mlogloss:0.36035	validation_1-mlogloss:0.99644
[48]	validation_0-mlogloss:0.35953	validation_1-mlogloss:1.00196
[49]	validation_0-mlogloss:0.35878	validation_1-mlogloss:1.00600
[50]	validation_0-mlogloss:0.35750	validation_1-mlogloss:1.00825
[51]	validation_0-mlogloss:0.35710	validation_1-mlogloss:1.01235
[52]	validation_0-mlogloss:0.35552	validation_1-mlogloss:1.01586
[53]	validation_0-mlogloss:0.35441	validation_1-mlogloss:1.01806
[54]	validation_0-mlogloss:0.35315	validation_1-mlogloss:1.01962
[55]	validation_0-mlogloss:0.35020	validation_1-mlogloss:1.02012
[56]	validation_0-mlogloss:0.34755	validation_1-mlogloss:1.01685
[57]	validation_0-mlogloss:0.34890	validation_1-mlogloss:1.01466
[58]	validation_0-mlogloss:0.34791	validation_1-mlogloss:1.01855
[59]	validation_0-mloglos

[26]	validation_0-mlogloss:0.43158	validation_1-mlogloss:0.99396
[27]	validation_0-mlogloss:0.42529	validation_1-mlogloss:1.00139
[28]	validation_0-mlogloss:0.42139	validation_1-mlogloss:1.00669
[29]	validation_0-mlogloss:0.41638	validation_1-mlogloss:1.01319
[30]	validation_0-mlogloss:0.41143	validation_1-mlogloss:1.02021
[31]	validation_0-mlogloss:0.40622	validation_1-mlogloss:1.02517
[32]	validation_0-mlogloss:0.40239	validation_1-mlogloss:1.03016
[33]	validation_0-mlogloss:0.39882	validation_1-mlogloss:1.03219
[34]	validation_0-mlogloss:0.39610	validation_1-mlogloss:1.03455
[35]	validation_0-mlogloss:0.39260	validation_1-mlogloss:1.03705
[36]	validation_0-mlogloss:0.39127	validation_1-mlogloss:1.03904
[37]	validation_0-mlogloss:0.38788	validation_1-mlogloss:1.04276
[38]	validation_0-mlogloss:0.38583	validation_1-mlogloss:1.04801
[39]	validation_0-mlogloss:0.38504	validation_1-mlogloss:1.05263
[40]	validation_0-mlogloss:0.38366	validation_1-mlogloss:1.05193
[41]	validation_0-mloglos

In [121]:
preds = pd.DataFrame(preds)
preds.index = a_index
preds

0
3    1
4    1
5    1
6    1
7    1
..  ..
284  1
285  1
286  1
292  1
293  1

[67 rows x 1 columns]

In [122]:
preds.describe()

0
count  67.000000
mean    1.119403
std     0.370192
min     0.000000
25%     1.000000
50%     1.000000
75%     1.000000
max     2.000000

# 데이터 준비

train데이터로 학습한 모델로 test데이터의 예측을 진행하므로 train의 컬럼만 test데이터에 넣는다.

train과 test 데이터는 필요없는 컬럼들 제거하고 knn 보간법으로 결측치 처리된 데이터

In [ ]:
testa_df = test_a[traina_pp.columns]
testto_df = test_to[trainto_pp.columns]

In [123]:
train_y = train_to['Y_Class']

In [124]:
train_x = pd.concat([train_to[['LINE', 'PRODUCT_CODE']],trainto_pp], axis = 1)
train_x.head()

LINE PRODUCT_CODE  X_1    X_2   X_5   X_7   X_8   X_11  X_15   X_16  \
0  T100304         T_31  2.0  102.0  11.0  45.0  10.0  514.4   0.0  247.5   
1  T100304         T_31  2.0  102.0  11.0  45.0  10.0  514.6   0.0  247.6   
2  T100304         T_31  2.0   97.0  11.0  45.0  10.0  517.4   0.0  247.5   
3  T100306         T_31  2.0   95.0  10.0  54.0  10.0  477.4   0.0  247.5   
4  T100304         T_31  2.0  100.0  11.0  45.0  10.0  516.5   0.0  247.6   

   ...  X_901  X_902     X_903  X_904  X_906      X_907  X_908  X_931  \
0  ...   10.0    9.0  9.000000    9.0  17.28  17.277333  17.27   13.7   
1  ...    8.0    9.0  8.883871    8.6  17.28  17.276508  17.27   13.7   
2  ...   11.0    9.0  8.516129    8.0  17.28  17.276452  17.27   13.7   
3  ...   12.0    9.0  8.387097    8.0  17.28  17.276452  17.27   13.7   
4  ...   11.0    9.0  8.903226    8.0  17.28  17.277419  17.27   13.7   

       X_932  X_933  
0  13.443333  13.20  
1  13.453484  13.24  
2  13.454839  13.20  
3  13.461290  13.30  
4  13.422581  13.20  

[5 rows x 286 columns]

In [125]:
test_x = pd.concat([test_to[['LINE', 'PRODUCT_CODE']],testto_df], axis = 1)
test_x.head()

LINE PRODUCT_CODE  X_1    X_2   X_5   X_7   X_8   X_11  X_15   X_16  \
0   T100306         T_31  2.0   94.0  10.0  51.0  10.0  469.6   0.0  247.5   
1   T100304         T_31  2.0   93.0  11.0  45.0  10.0  506.6   0.0  247.6   
2   T100304         T_31  2.0   95.0  11.0  45.0  10.0  506.6   0.0  247.6   
15  T100304         T_31  2.0  102.0  11.0  45.0  10.0  520.3   0.0  247.5   
16  T100306         T_31  2.0   93.0  10.0  54.0  10.0  472.5   0.0  247.5   

    ...  X_901  X_902  X_903  X_904  X_906      X_907  X_908  X_931  \
0   ...   10.0    9.0    9.0    9.0  17.28  17.278387  17.27   13.6   
1   ...   10.0    9.0    9.0    9.0  17.28  17.277742  17.27   13.6   
2   ...    8.0    9.0    9.0    9.0  17.28  17.277097  17.27   13.6   
15  ...   10.0    9.0    9.0    9.0  17.28  17.276774  17.27   13.6   
16  ...   11.0    9.0    9.0    9.0  17.28  17.275806  17.27   13.6   

        X_932  X_933  
0   13.383871   13.2  
1   13.406452   13.2  
2   13.370968   13.2  
15  13.387097   13.2  
16  13.367742   13.2  

[5 rows x 286 columns]

In [126]:
to_index = test_x.index.tolist() 

### TO 데이터 범주형 변수 라벨 인코딩

In [127]:
qual_col = ['LINE', 'PRODUCT_CODE']

for i in qual_col:
    le = LabelEncoder()
    le = le.fit(train_x[i]) #원래 column 값을 기준으로 fit.
    train_x[i] = le.transform(train_x[i]) #수치화, 수치로 변형

    for label in np.unique(test_x[i]): 
        if label not in le.classes_: 
            le.classes_ = np.append(le.classes_, label)
    test_x[i] = le.transform(test_x[i]) 
print('Done.')

Done.


## train_to 학습 및 test_to 예측

In [128]:
from xgboost import XGBClassifier
from sklearn.model_selection import GridSearchCV

xgb_model = XGBClassifier(n_estimators=1500)

X_train, X_test, y_train, y_test = train_test_split(train_x, train_y, 
                                                    test_size=0.3, 
                                                    stratify=train_y, 
                                                    random_state=37)

params = {'max_depth':[5, 6, 7], #일반적으로 3~10
          'subsample':[0.75, 0.8, 0.85], #일반적으로 0.5 ~ 1
          'learning_rate':[0.08, 0.1, 0.12], #일반적으로 0.01 ~ 0.2
          'min_child_weight':[3], # 1보다 샘플수작으면 leaf node. 너무 크게 설정하면 언더피팅
          'reg_lambda': [1], #default 1, L2 규제
          'reg_alpha' : [0.2], #default 0, L1 규제  
          'min_split_loss':[0.05, 0.1, 0.15], #범위 0~무한대
          'colsample_bytree':[0.8, 0.9]} #일반적으로 0~1

# gridsearchcv 객체 정보 입력(어떤 모델, 파라미터 후보, 교차검증 몇 번)
gridcv = GridSearchCV(xgb_model, param_grid=params, cv=3)

# 파라미터 튜닝 시작 / eval_set: 학습은  (X_train, y_train), 검증은 (X_test, y_test)
gridcv.fit(X_train, y_train, early_stopping_rounds=50, eval_metric='mlogloss', eval_set=[(X_train, y_train), (X_test, y_test)])

#튜닝된 파라미터 출력
print(gridcv.best_params_)
print(gridcv.best_score_)

best_params = gridcv.best_params_
best_xgb_model = XGBClassifier(n_estimators=1500, **best_params)

# 훈련 데이터 전체에 대해 모델 학습
best_xgb_model.fit(X_train, y_train)

# 새로운 데이터에 대해 예측
preds2 = best_xgb_model.predict(test_x)

[0]	validation_0-mlogloss:1.02280	validation_1-mlogloss:1.02917
[1]	validation_0-mlogloss:0.96310	validation_1-mlogloss:0.97690
[2]	validation_0-mlogloss:0.90916	validation_1-mlogloss:0.93474
[3]	validation_0-mlogloss:0.85994	validation_1-mlogloss:0.89303
[4]	validation_0-mlogloss:0.81628	validation_1-mlogloss:0.85786
[5]	validation_0-mlogloss:0.77760	validation_1-mlogloss:0.82764
[6]	validation_0-mlogloss:0.74013	validation_1-mlogloss:0.79434
[7]	validation_0-mlogloss:0.70679	validation_1-mlogloss:0.76670
[8]	validation_0-mlogloss:0.67513	validation_1-mlogloss:0.74244
[9]	validation_0-mlogloss:0.64894	validation_1-mlogloss:0.72090
[10]	validation_0-mlogloss:0.62433	validation_1-mlogloss:0.69809
[11]	validation_0-mlogloss:0.60129	validation_1-mlogloss:0.68002
[12]	validation_0-mlogloss:0.57816	validation_1-mlogloss:0.66518
[13]	validation_0-mlogloss:0.55765	validation_1-mlogloss:0.64634
[14]	validation_0-mlogloss:0.53922	validation_1-mlogloss:0.63276
[15]	validation_0-mlogloss:0.52368	

[44]	validation_0-mlogloss:0.30391	validation_1-mlogloss:0.59759
[45]	validation_0-mlogloss:0.30117	validation_1-mlogloss:0.59986
[46]	validation_0-mlogloss:0.29810	validation_1-mlogloss:0.60112
[47]	validation_0-mlogloss:0.29486	validation_1-mlogloss:0.60329
[48]	validation_0-mlogloss:0.29295	validation_1-mlogloss:0.60289
[49]	validation_0-mlogloss:0.29058	validation_1-mlogloss:0.60363
[50]	validation_0-mlogloss:0.28942	validation_1-mlogloss:0.60642
[51]	validation_0-mlogloss:0.28805	validation_1-mlogloss:0.60789
[52]	validation_0-mlogloss:0.28559	validation_1-mlogloss:0.60801
[53]	validation_0-mlogloss:0.28471	validation_1-mlogloss:0.60864
[54]	validation_0-mlogloss:0.28278	validation_1-mlogloss:0.61061
[55]	validation_0-mlogloss:0.28097	validation_1-mlogloss:0.61310
[56]	validation_0-mlogloss:0.27944	validation_1-mlogloss:0.61475
[57]	validation_0-mlogloss:0.27749	validation_1-mlogloss:0.61634
[58]	validation_0-mlogloss:0.27648	validation_1-mlogloss:0.61885
[59]	validation_0-mloglos

[87]	validation_0-mlogloss:0.25837	validation_1-mlogloss:0.61922
[88]	validation_0-mlogloss:0.25748	validation_1-mlogloss:0.61890
[89]	validation_0-mlogloss:0.25706	validation_1-mlogloss:0.62031
[90]	validation_0-mlogloss:0.25698	validation_1-mlogloss:0.62101
[91]	validation_0-mlogloss:0.25623	validation_1-mlogloss:0.62335
[92]	validation_0-mlogloss:0.25600	validation_1-mlogloss:0.62464
[93]	validation_0-mlogloss:0.25557	validation_1-mlogloss:0.62593
[0]	validation_0-mlogloss:1.02238	validation_1-mlogloss:1.03326
[1]	validation_0-mlogloss:0.96028	validation_1-mlogloss:0.98276
[2]	validation_0-mlogloss:0.90315	validation_1-mlogloss:0.93948
[3]	validation_0-mlogloss:0.85085	validation_1-mlogloss:0.89664
[4]	validation_0-mlogloss:0.80456	validation_1-mlogloss:0.85660
[5]	validation_0-mlogloss:0.76504	validation_1-mlogloss:0.82668
[6]	validation_0-mlogloss:0.72801	validation_1-mlogloss:0.79409
[7]	validation_0-mlogloss:0.69444	validation_1-mlogloss:0.76856
[8]	validation_0-mlogloss:0.66274

[43]	validation_0-mlogloss:0.29485	validation_1-mlogloss:0.57205
[44]	validation_0-mlogloss:0.29270	validation_1-mlogloss:0.57366
[45]	validation_0-mlogloss:0.29049	validation_1-mlogloss:0.57538
[46]	validation_0-mlogloss:0.28822	validation_1-mlogloss:0.57707
[47]	validation_0-mlogloss:0.28532	validation_1-mlogloss:0.57920
[48]	validation_0-mlogloss:0.28360	validation_1-mlogloss:0.57906
[49]	validation_0-mlogloss:0.28166	validation_1-mlogloss:0.57972
[50]	validation_0-mlogloss:0.28079	validation_1-mlogloss:0.58215
[51]	validation_0-mlogloss:0.27911	validation_1-mlogloss:0.58390
[52]	validation_0-mlogloss:0.27715	validation_1-mlogloss:0.58407
[53]	validation_0-mlogloss:0.27594	validation_1-mlogloss:0.58536
[54]	validation_0-mlogloss:0.27481	validation_1-mlogloss:0.58791
[55]	validation_0-mlogloss:0.27278	validation_1-mlogloss:0.58912
[56]	validation_0-mlogloss:0.27195	validation_1-mlogloss:0.59176
[57]	validation_0-mlogloss:0.27143	validation_1-mlogloss:0.59282
[58]	validation_0-mloglos

[85]	validation_0-mlogloss:0.25519	validation_1-mlogloss:0.62639
[0]	validation_0-mlogloss:1.02125	validation_1-mlogloss:1.03230
[1]	validation_0-mlogloss:0.96001	validation_1-mlogloss:0.98149
[2]	validation_0-mlogloss:0.90026	validation_1-mlogloss:0.93635
[3]	validation_0-mlogloss:0.84862	validation_1-mlogloss:0.89406
[4]	validation_0-mlogloss:0.80101	validation_1-mlogloss:0.85713
[5]	validation_0-mlogloss:0.76137	validation_1-mlogloss:0.82714
[6]	validation_0-mlogloss:0.72421	validation_1-mlogloss:0.79796
[7]	validation_0-mlogloss:0.68858	validation_1-mlogloss:0.77286
[8]	validation_0-mlogloss:0.65648	validation_1-mlogloss:0.74823
[9]	validation_0-mlogloss:0.62971	validation_1-mlogloss:0.72582
[10]	validation_0-mlogloss:0.60338	validation_1-mlogloss:0.70565
[11]	validation_0-mlogloss:0.57874	validation_1-mlogloss:0.68728
[12]	validation_0-mlogloss:0.55603	validation_1-mlogloss:0.67149
[13]	validation_0-mlogloss:0.53556	validation_1-mlogloss:0.65721
[14]	validation_0-mlogloss:0.51717	

...

[50]	validation_0-mlogloss:0.26400	validation_1-mlogloss:0.62673
[51]	validation_0-mlogloss:0.26328	validation_1-mlogloss:0.62826
[52]	validation_0-mlogloss:0.26170	validation_1-mlogloss:0.62889
[53]	validation_0-mlogloss:0.26094	validation_1-mlogloss:0.62890
[54]	validation_0-mlogloss:0.26039	validation_1-mlogloss:0.63004
[55]	validation_0-mlogloss:0.26032	validation_1-mlogloss:0.63095
[56]	validation_0-mlogloss:0.26018	validation_1-mlogloss:0.63338
[57]	validation_0-mlogloss:0.25930	validation_1-mlogloss:0.63455
[58]	validation_0-mlogloss:0.25814	validation_1-mlogloss:0.63776
[59]	validation_0-mlogloss:0.25758	validation_1-mlogloss:0.64181
[60]	validation_0-mlogloss:0.25765	validation_1-mlogloss:0.64486
[61]	validation_0-mlogloss:0.25645	validation_1-mlogloss:0.64325
[62]	validation_0-mlogloss:0.25569	validation_1-mlogloss:0.64415
[63]	validation_0-mlogloss:0.25477	validation_1-mlogloss:0.64487
[64]	validation_0-mlogloss:0.25469	validation_1-mlogloss:0.64760
[65]	validation_0-mloglos

[34]	validation_0-mlogloss:0.27108	validation_1-mlogloss:0.59677
[35]	validation_0-mlogloss:0.26949	validation_1-mlogloss:0.59779
[36]	validation_0-mlogloss:0.26729	validation_1-mlogloss:0.59831
[37]	validation_0-mlogloss:0.26582	validation_1-mlogloss:0.60164
[38]	validation_0-mlogloss:0.26457	validation_1-mlogloss:0.60295
[39]	validation_0-mlogloss:0.26268	validation_1-mlogloss:0.60684
[40]	validation_0-mlogloss:0.26218	validation_1-mlogloss:0.60717
[41]	validation_0-mlogloss:0.26056	validation_1-mlogloss:0.60962
[42]	validation_0-mlogloss:0.25874	validation_1-mlogloss:0.61126
[43]	validation_0-mlogloss:0.25704	validation_1-mlogloss:0.61210
[44]	validation_0-mlogloss:0.25533	validation_1-mlogloss:0.61400
[45]	validation_0-mlogloss:0.25469	validation_1-mlogloss:0.61730
[46]	validation_0-mlogloss:0.25301	validation_1-mlogloss:0.61803
[47]	validation_0-mlogloss:0.25184	validation_1-mlogloss:0.62083
[48]	validation_0-mlogloss:0.25106	validation_1-mlogloss:0.62107
[49]	validation_0-mloglos

[13]	validation_0-mlogloss:0.42189	validation_1-mlogloss:0.59009
[14]	validation_0-mlogloss:0.40639	validation_1-mlogloss:0.58103
[15]	validation_0-mlogloss:0.39040	validation_1-mlogloss:0.57734
[16]	validation_0-mlogloss:0.37876	validation_1-mlogloss:0.57206
[17]	validation_0-mlogloss:0.36715	validation_1-mlogloss:0.57098
[18]	validation_0-mlogloss:0.35577	validation_1-mlogloss:0.56947
[19]	validation_0-mlogloss:0.34560	validation_1-mlogloss:0.56683
[20]	validation_0-mlogloss:0.33776	validation_1-mlogloss:0.56534
[21]	validation_0-mlogloss:0.33105	validation_1-mlogloss:0.56675
[22]	validation_0-mlogloss:0.32359	validation_1-mlogloss:0.56858
[23]	validation_0-mlogloss:0.31798	validation_1-mlogloss:0.57088
[24]	validation_0-mlogloss:0.31374	validation_1-mlogloss:0.57305
[25]	validation_0-mlogloss:0.30882	validation_1-mlogloss:0.57609
[26]	validation_0-mlogloss:0.30451	validation_1-mlogloss:0.57783
[27]	validation_0-mlogloss:0.30101	validation_1-mlogloss:0.57979
[28]	validation_0-mloglos

[0]	validation_0-mlogloss:0.99276	validation_1-mlogloss:1.01088
[1]	validation_0-mlogloss:0.90384	validation_1-mlogloss:0.92851
[2]	validation_0-mlogloss:0.82639	validation_1-mlogloss:0.86620
[3]	validation_0-mlogloss:0.76043	validation_1-mlogloss:0.81984
[4]	validation_0-mlogloss:0.70523	validation_1-mlogloss:0.77862
[5]	validation_0-mlogloss:0.65584	validation_1-mlogloss:0.74284
[6]	validation_0-mlogloss:0.61077	validation_1-mlogloss:0.70899
[7]	validation_0-mlogloss:0.57418	validation_1-mlogloss:0.68607
[8]	validation_0-mlogloss:0.53930	validation_1-mlogloss:0.66342
[9]	validation_0-mlogloss:0.51169	validation_1-mlogloss:0.64620
[10]	validation_0-mlogloss:0.48697	validation_1-mlogloss:0.63220
[11]	validation_0-mlogloss:0.46436	validation_1-mlogloss:0.61950
[12]	validation_0-mlogloss:0.44209	validation_1-mlogloss:0.61234
[13]	validation_0-mlogloss:0.42467	validation_1-mlogloss:0.60145
[14]	validation_0-mlogloss:0.40845	validation_1-mlogloss:0.59337
[15]	validation_0-mlogloss:0.39483	

[52]	validation_0-mlogloss:0.12381	validation_1-mlogloss:0.59468
[53]	validation_0-mlogloss:0.12099	validation_1-mlogloss:0.59889
[54]	validation_0-mlogloss:0.11852	validation_1-mlogloss:0.60101
[55]	validation_0-mlogloss:0.11603	validation_1-mlogloss:0.60262
[56]	validation_0-mlogloss:0.11358	validation_1-mlogloss:0.60379
[57]	validation_0-mlogloss:0.11121	validation_1-mlogloss:0.60600
[58]	validation_0-mlogloss:0.10887	validation_1-mlogloss:0.60619
[59]	validation_0-mlogloss:0.10688	validation_1-mlogloss:0.60742
[60]	validation_0-mlogloss:0.10503	validation_1-mlogloss:0.60918
[61]	validation_0-mlogloss:0.10300	validation_1-mlogloss:0.61068
[62]	validation_0-mlogloss:0.10094	validation_1-mlogloss:0.61204
[63]	validation_0-mlogloss:0.09895	validation_1-mlogloss:0.61431
[64]	validation_0-mlogloss:0.09700	validation_1-mlogloss:0.61741
[65]	validation_0-mlogloss:0.09510	validation_1-mlogloss:0.62166
[66]	validation_0-mlogloss:0.09331	validation_1-mlogloss:0.62269
[67]	validation_0-mloglos

In [129]:
preds2 = pd.DataFrame(preds2)
preds2.index = to_index
preds2

0
0    1
1    1
2    1
15   1
16   1
..  ..
305  1
306  1
307  1
308  1
309  1

[243 rows x 1 columns]

In [130]:
preds2.describe()

0
count  243.000000
mean     1.020576
std      0.142253
min      1.000000
25%      1.000000
50%      1.000000
75%      1.000000
max      2.000000

In [131]:
prediction = pd.concat([preds, preds2], axis = 0)
prediction = prediction.sort_index(ascending=True)
prediction

0
0    1
1    1
2    1
3    1
4    1
..  ..
305  1
306  1
307  1
308  1
309  1

[310 rows x 1 columns]

In [132]:
prediction.describe()

0
count  310.000000
mean     1.041935
std      0.216285
min      0.000000
25%      1.000000
50%      1.000000
75%      1.000000
max      2.000000

In [133]:
sub = pd.read_csv('./sample_submission.csv')
sub['Y_Class'] = prediction
#이상치처리x, 결측치knn보간법, std0제거, 높은 상관성 제거, test data 결측치 처리x
sub.to_csv('./data/sub/sub_grid2.csv', index = False)

In [134]:
!jupyter nbconvert --clear-output --inplace 3_ModelTraining_xgboost_grid.ipynb

[NbConvertApp] Converting notebook 3_ModelTraining_xgboost_grid.ipynb to notebook
[NbConvertApp] Writing 16002 bytes to 3_ModelTraining_xgboost_grid.ipynb
